## **Information Retrieval Systems Week 3 Homework**
### ***Comparing Linear Search Approach with Vector Space Model Approach in Search Efficiency***

### **Import and Prepare Data**
First of all, we need to import the dataset and prepare for further processes.

In [ ]:
from google.colab import files
uploaded = files.upload()

!unzip /content/75haber.zip -d /content

!rm -fr /content/75haber/text*
!rm -f /content/75haber/okubeni.doc
!mv /content/75haber/raw_texts/* /content/75haber/
!rm -fr /content/75haber/raw_texts

Now, let's check the data

In [ ]:
!apt-get install tree

!tree /content/75haber

### **Defining Common Variables for Both Approaches**
There are variables that will be used by both approaches, such as dataset path and document paths. Also, test queries and the dictionary that we will use to save and compare the time complexities named "results" are going to be commonly used as well, so they are defined and initiated in this section.

In [142]:
import os
import time

dataset_path = "./content/75haber";

# Gathering document paths
doc_paths = [];
for category in os.listdir(dataset_path):
   for file in os.listdir(os.path.join(dataset_path, category)):
      if file.endswith('.txt'):
        doc_paths.append(os.path.join(dataset_path, category, file));

# Example queries
queries = ["Fenerbahçe", "2006", "Bilim", "Türkiye", "Spor", "Lale"]

# Results for time measurement
results = {"Fenerbahçe": {"linear":0, "vector_space":0},
           "2006":  {"linear":0, "vector_space":0},
            "Bilim":  {"linear":0, "vector_space":0},
            "Türkiye":  {"linear":0, "vector_space":0},
            "Spor":  {"linear":0, "vector_space":0},
            "Lale":  {"linear":0, "vector_space":0}}

### **Linear Search Approach**
This approach uses the linear search algorithm. It is not efficient since it compares the query with all documents in the dataset by opening each document and reading its content every time.

#### Defining Linear Search Function

In [143]:
def linear_search_in_docs(search_string):
    start_time = time.perf_counter_ns()

    for file_name in doc_paths:
        with open(file_name, 'rb') as f:
            file_contents = f.read().decode('iso-8859-9');

        if search_string in file_contents:
            print(f"Linear Search found '{search_string}' in file '{file_name}'.")
    end_time = time.perf_counter_ns()
    return ((end_time - start_time))

### **Vector Space Model Approach**
This approach uses the vector space model. It is much more efficient in terms of time complexity, but a bit more complex than the linear search. Also loading all the data is a little expensive in terms of memory.

#### Creating The Corpus

In [144]:
# Preparing corpus
corpus = [];

for file_name in doc_paths:
    with open(file_name, 'rb') as f:
        corpus.append(f.read().decode('iso-8859-9'));

corpus_tokens = [ doc.split() for doc in corpus ];
corpus_tokens


[["'Fener",
  "Cumhuriyeti'nin",
  'geliri',
  'borcunun',
  'iki',
  'katı',
  'Fenerbahçe',
  'Başkanı',
  'Aziz',
  'Yıldırım,',
  'kulübün',
  "2006'ya",
  'kadar',
  '65',
  'milyon',
  'dolar',
  'borç',
  'ödemesi',
  'bulunduğunu',
  'söyledi.',
  'Yıldırım,',
  'ancak',
  'borcun',
  '2',
  'katı',
  'kadar',
  'da',
  'gelir',
  'beklendiğini',
  'açıkladı',
  'EKONOMİ',
  'SERVİSİ',
  'Fenerbahçe',
  'Kulübü',
  'Başkanı',
  'Aziz',
  'Yıldırım,',
  'kulübün',
  '2006',
  'yılına',
  'kadar',
  'mukavelelere',
  'bağlanmış',
  'borçlarının',
  '65',
  'milyon',
  'dolar',
  'olduğunu',
  'belirterek,',
  "''Kulübün",
  'aynı',
  'sürede',
  '2',
  'katı',
  'kadar',
  'geliri',
  've',
  'alacağı',
  'var.',
  'Şu',
  'anda',
  'alacak',
  've',
  'borçları',
  'bir',
  'araya',
  'getirilirse',
  'hep',
  'artıda',
  'olan',
  'bir',
  "kulüp''",
  'dedi.',
  'Fenerbahçe',
  'Sportif',
  'AŞ',
  'hisselerinin',
  'halka',
  'arzıyla',
  'ilgili',
  'yapılan',
  'anlaşmanın'

#### Creating The Flattened Tokens

In [145]:
tokens_flat = [x for X in corpus_tokens for x in X]
print("Flattened tokens =  {}".format(tokens_flat))

Flattened tokens =  ["'Fener", "Cumhuriyeti'nin", 'geliri', 'borcunun', 'iki', 'katı', 'Fenerbahçe', 'Başkanı', 'Aziz', 'Yıldırım,', 'kulübün', "2006'ya", 'kadar', '65', 'milyon', 'dolar', 'borç', 'ödemesi', 'bulunduğunu', 'söyledi.', 'Yıldırım,', 'ancak', 'borcun', '2', 'katı', 'kadar', 'da', 'gelir', 'beklendiğini', 'açıkladı', 'EKONOMİ', 'SERVİSİ', 'Fenerbahçe', 'Kulübü', 'Başkanı', 'Aziz', 'Yıldırım,', 'kulübün', '2006', 'yılına', 'kadar', 'mukavelelere', 'bağlanmış', 'borçlarının', '65', 'milyon', 'dolar', 'olduğunu', 'belirterek,', "''Kulübün", 'aynı', 'sürede', '2', 'katı', 'kadar', 'geliri', 've', 'alacağı', 'var.', 'Şu', 'anda', 'alacak', 've', 'borçları', 'bir', 'araya', 'getirilirse', 'hep', 'artıda', 'olan', 'bir', "kulüp''", 'dedi.', 'Fenerbahçe', 'Sportif', 'AŞ', 'hisselerinin', 'halka', 'arzıyla', 'ilgili', 'yapılan', 'anlaşmanın', 'imza', 'töreninde,', "''Fenerbahçe", 'Cumhuriyeti', 'Halka', 'Açılıyor,', 'Cumhuriyet', "Halkındır''", 'temalı', 'multivizyon', 'gösterisi',

#### Creating The Vocabulary

In [170]:
vocab = set(tokens_flat)
print("Size of vocabulary %d" % len(vocab) )
print("Vocabulary: %s" % vocab)

Size of vocabulary 8509
Vocabulary: {'uymadığına', 'denetim', 'benim', 'Dk.46)(Czinege', 'Asgari', 'kahvaltılık,', 'diyafram', 'a', "Baykal'la", 'Grubu', 'prim', 'olacak', 'gelecektir', "Çamardı'ya", 'bulaşmamış', 'çalıştığı,', "Internet'te", 'unsurların', 'acentalara', 'yıldan', 'programı,', '"merhaba"', 'talepte', "Baykal'ın", 'iç', 'bütçe', 'hisseleri', 'eşlerini', 'görüşmeler', 'Hayat', 'şiddetli', 'kadın', 'kamuoyuna', 'kullanımının,', 'yönünde.', "Galatasaraylılar'ın", 'olduğunun', 'belirten', "Bar'da", 'KARTAL', 'izlenen', '(AİBÜ)', 'Sevdiği', "Venedik'teki", 'müdürlüğüne,', 'Doğrudan', 'Özcan', 'karnımızı', 'KDV', '"kamu', 'alması', 'bozma', 'ortopedistler', 'örnekle', 'tasarruf', "IMF'nin,", "'Vanmour", 'aralarında', 'belirtti.', 'katkısını', 'genişletmeyi', 'terk', 'Arınç', 'geçirmeden', '(6)', 'üzerinde,', 'kolaylıklardan', 'bandı', 'etmek', 'marjinal', 'vakfın', '"doğalgaza', "Erdoğan'ın", 'başı', 'yanıtladı:', 'planladıkları', 'Bilgin', 'finalde', 'anarşiyi', 'meydana', 'k

#### Indexing

In [147]:
for idx, token in enumerate(vocab):
  print("index = %d \t  vocabulary term: %s" % (idx, token))

index = 0 	  vocabulary term: uymadığına
index = 1 	  vocabulary term: denetim
index = 2 	  vocabulary term: benim
index = 3 	  vocabulary term: Dk.46)(Czinege
index = 4 	  vocabulary term: Asgari
index = 5 	  vocabulary term: kahvaltılık,
index = 6 	  vocabulary term: diyafram
index = 7 	  vocabulary term: a
index = 8 	  vocabulary term: Baykal'la
index = 9 	  vocabulary term: Grubu
index = 10 	  vocabulary term: prim
index = 11 	  vocabulary term: olacak
index = 12 	  vocabulary term: gelecektir
index = 13 	  vocabulary term: Çamardı'ya
index = 14 	  vocabulary term: bulaşmamış
index = 15 	  vocabulary term: çalıştığı,
index = 16 	  vocabulary term: Internet'te
index = 17 	  vocabulary term: unsurların
index = 18 	  vocabulary term: acentalara
index = 19 	  vocabulary term: yıldan
index = 20 	  vocabulary term: programı,
index = 21 	  vocabulary term: "merhaba"
index = 22 	  vocabulary term: talepte
index = 23 	  vocabulary term: Baykal'ın
index = 24 	  vocabulary term: iç
index = 25

In [148]:
term2idx = {};
for idx, token in enumerate(vocab):
  term2idx.update({token:idx})

print(term2idx)

{'uymadığına': 0, 'denetim': 1, 'benim': 2, 'Dk.46)(Czinege': 3, 'Asgari': 4, 'kahvaltılık,': 5, 'diyafram': 6, 'a': 7, "Baykal'la": 8, 'Grubu': 9, 'prim': 10, 'olacak': 11, 'gelecektir': 12, "Çamardı'ya": 13, 'bulaşmamış': 14, 'çalıştığı,': 15, "Internet'te": 16, 'unsurların': 17, 'acentalara': 18, 'yıldan': 19, 'programı,': 20, '"merhaba"': 21, 'talepte': 22, "Baykal'ın": 23, 'iç': 24, 'bütçe': 25, 'hisseleri': 26, 'eşlerini': 27, 'görüşmeler': 28, 'Hayat': 29, 'şiddetli': 30, 'kadın': 31, 'kamuoyuna': 32, 'kullanımının,': 33, 'yönünde.': 34, "Galatasaraylılar'ın": 35, 'olduğunun': 36, 'belirten': 37, "Bar'da": 38, 'KARTAL': 39, 'izlenen': 40, '(AİBÜ)': 41, 'Sevdiği': 42, "Venedik'teki": 43, 'müdürlüğüne,': 44, 'Doğrudan': 45, 'Özcan': 46, 'karnımızı': 47, 'KDV': 48, '"kamu': 49, 'alması': 50, 'bozma': 51, 'ortopedistler': 52, 'örnekle': 53, 'tasarruf': 54, "IMF'nin,": 55, "'Vanmour": 56, 'aralarında': 57, 'belirtti.': 58, 'katkısını': 59, 'genişletmeyi': 60, 'terk': 61, 'Arınç': 62,

In [149]:
idx2term = {};
for term in term2idx:
  idx = term2idx.get(term);
  idx2term.update({idx:term});
print(idx2term);

{0: 'uymadığına', 1: 'denetim', 2: 'benim', 3: 'Dk.46)(Czinege', 4: 'Asgari', 5: 'kahvaltılık,', 6: 'diyafram', 7: 'a', 8: "Baykal'la", 9: 'Grubu', 10: 'prim', 11: 'olacak', 12: 'gelecektir', 13: "Çamardı'ya", 14: 'bulaşmamış', 15: 'çalıştığı,', 16: "Internet'te", 17: 'unsurların', 18: 'acentalara', 19: 'yıldan', 20: 'programı,', 21: '"merhaba"', 22: 'talepte', 23: "Baykal'ın", 24: 'iç', 25: 'bütçe', 26: 'hisseleri', 27: 'eşlerini', 28: 'görüşmeler', 29: 'Hayat', 30: 'şiddetli', 31: 'kadın', 32: 'kamuoyuna', 33: 'kullanımının,', 34: 'yönünde.', 35: "Galatasaraylılar'ın", 36: 'olduğunun', 37: 'belirten', 38: "Bar'da", 39: 'KARTAL', 40: 'izlenen', 41: '(AİBÜ)', 42: 'Sevdiği', 43: "Venedik'teki", 44: 'müdürlüğüne,', 45: 'Doğrudan', 46: 'Özcan', 47: 'karnımızı', 48: 'KDV', 49: '"kamu', 50: 'alması', 51: 'bozma', 52: 'ortopedistler', 53: 'örnekle', 54: 'tasarruf', 55: "IMF'nin,", 56: "'Vanmour", 57: 'aralarında', 58: 'belirtti.', 59: 'katkısını', 60: 'genişletmeyi', 61: 'terk', 62: 'Arınç',

#### Creating a List of Document Vectors

In [150]:
docvec_list = [];
for doc in corpus:
  doc_vec = [];
  for idx in idx2term:
    if doc.find(idx2term.get(idx)) > -1:
       doc_vec.append(1);
    else:
       doc_vec.append(0);
  docvec_list.append(doc_vec);

docvec_list

[[0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  1,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  1,
  0,
  0,
  0,
  0,
  1,
  1,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,


#### Creating the Matrix

In [151]:
matrix = [[doc_vec[j] for doc_vec in docvec_list] for j in range(len(vocab))]

In [152]:
print("\t\t", end="")
for a in range(0,len(matrix[0])):
  print("{}\t".format(doc_paths[a].split("\\")[-1]), end="")
print();

for idx, row in enumerate(matrix):
  print(idx2term.get(idx), end="\t");
  
  if len(idx2term.get(idx)) < 8: print(end="\t");

  for does_contain in row:
    print(does_contain, end="\t");
  print();

		e1.txt	e10.txt	e2.txt	e3.txt	e4.txt	e5.txt	e6.txt	e7.txt	e8.txt	e9.txt	t1.txt	t2.txt	t3.txt	t4.txt	t5.txt	e11.txt	e12.txt	e13.txt	e14.txt	e15.txt	e16.txt	e17.txt	e18.txt	e19.txt	e20.txt	t10.txt	t6.txt	t7.txt	t8.txt	t9.txt	e21.txt	e22.txt	e23.txt	e24.txt	e25.txt	e26.txt	e27.txt	e28.txt	e29.txt	e30.txt	t11.txt	t12.txt	t13.txt	t14.txt	t15.txt	e31.txt	e32.txt	e33.txt	e34.txt	e35.txt	e36.txt	e37.txt	e38.txt	e39.txt	e40.txt	t16.txt	t17.txt	t18.txt	t19.txt	t20.txt	e41.txt	e42.txt	e43.txt	e44.txt	e45.txt	e46.txt	e47.txt	e48.txt	e49.txt	e50.txt	t21.txt	t22.txt	t23.txt	t24.txt	t25.txt	
uymadığına	0	0	0	1	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	
denetim		0	0	0	0	0	0	0	0	1	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	
benim		0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	0	1	0	0	1	0	0	0	0	0	0	0	0	0	0	1	0	0	0	0	0	0	0	0	0	0	

#### Defining Vector Space Search Function

In [154]:
def vector_space_search_in_docs(search_string):
    start_time = time.perf_counter_ns()

    term_list = matrix[term2idx.get(search_string)]

    for idx, term in enumerate(term_list):
        if term == 1:
            print(f"Vector Space Model found '{search_string}' in file '{doc_paths[idx]}'.")
    
    end_time = time.perf_counter_ns()
    return ((end_time - start_time))

### **Comparison Results and Conclusion**
This part is where we compare the results in terms of time complexity. We already know that using the vector space model approach in theory is much better when compared to linear search approach. We will see whether that is the case or not.

In [159]:
# Saving results for linear search approach
for query in queries:
    query_res = linear_search_in_docs(query)
    results[query]["linear"] = ("{} ms").format(linear_search_in_docs(query))

Linear Search found 'Fenerbahçe' in file './content/75haber\ekonomi\e1.txt'.
Linear Search found 'Fenerbahçe' in file './content/75haber\magazin\e16.txt'.
Linear Search found 'Fenerbahçe' in file './content/75haber\spor\e47.txt'.
Linear Search found 'Fenerbahçe' in file './content/75haber\spor\e50.txt'.
Linear Search found 'Fenerbahçe' in file './content/75haber\ekonomi\e1.txt'.
Linear Search found 'Fenerbahçe' in file './content/75haber\magazin\e16.txt'.
Linear Search found 'Fenerbahçe' in file './content/75haber\spor\e47.txt'.
Linear Search found 'Fenerbahçe' in file './content/75haber\spor\e50.txt'.
Linear Search found '2006' in file './content/75haber\ekonomi\e1.txt'.
Linear Search found '2006' in file './content/75haber\ekonomi\e1.txt'.
Linear Search found 'Bilim' in file './content/75haber\saglik\e21.txt'.
Linear Search found 'Bilim' in file './content/75haber\saglik\t13.txt'.
Linear Search found 'Bilim' in file './content/75haber\saglik\e21.txt'.
Linear Search found 'Bilim' in f

In [160]:
# Saving results for vector space model approach
for query in queries:
    query_res = vector_space_search_in_docs(query)
    results[query]["vector_space"] = ("{} ms").format(vector_space_search_in_docs(query))

Vector Space Model found 'Fenerbahçe' in file './content/75haber\ekonomi\e1.txt'.
Vector Space Model found 'Fenerbahçe' in file './content/75haber\magazin\e16.txt'.
Vector Space Model found 'Fenerbahçe' in file './content/75haber\spor\e47.txt'.
Vector Space Model found 'Fenerbahçe' in file './content/75haber\spor\e50.txt'.
Vector Space Model found 'Fenerbahçe' in file './content/75haber\ekonomi\e1.txt'.
Vector Space Model found 'Fenerbahçe' in file './content/75haber\magazin\e16.txt'.
Vector Space Model found 'Fenerbahçe' in file './content/75haber\spor\e47.txt'.
Vector Space Model found 'Fenerbahçe' in file './content/75haber\spor\e50.txt'.
Vector Space Model found '2006' in file './content/75haber\ekonomi\e1.txt'.
Vector Space Model found '2006' in file './content/75haber\ekonomi\e1.txt'.
Vector Space Model found 'Bilim' in file './content/75haber\saglik\e21.txt'.
Vector Space Model found 'Bilim' in file './content/75haber\saglik\t13.txt'.
Vector Space Model found 'Bilim' in file './

In [169]:
# Total time for linear search approach
total_time_linear = 0
for query in results:
    total_time_linear += int(results[query]["linear"].split(" ")[0])

# Total time for vector space model approach
total_time_vector_space = 0
for query in results:
    total_time_vector_space += int(results[query]["vector_space"].split(" ")[0])

# Printing results

for query in results:
    print("\nQuery: \"{}\" \nLinear search approach time : {} \nVector space model approach time : {}".format(query, results[query]["linear"], results[query]["vector_space"]))

print("\nTotal time for linear search approach: {} ms".format(total_time_linear))
print("Total time for vector space model approach: {} ms".format(total_time_vector_space))
print("Ratio: Vector Space Model approach is in overall {:.2f} times faster than Linear Search approach.".format(total_time_linear/total_time_vector_space))


Query: "Fenerbahçe" 
Linear search approach time : 8989500 ms 
Vector space model approach time : 46600 ms

Query: "2006" 
Linear search approach time : 8198300 ms 
Vector space model approach time : 8700 ms

Query: "Bilim" 
Linear search approach time : 9730100 ms 
Vector space model approach time : 12200 ms

Query: "Türkiye" 
Linear search approach time : 7627300 ms 
Vector space model approach time : 144100 ms

Query: "Spor" 
Linear search approach time : 5870900 ms 
Vector space model approach time : 17100 ms

Query: "Lale" 
Linear search approach time : 5707800 ms 
Vector space model approach time : 7800 ms

Total time for linear search approach: 46123900 ms
Total time for vector space model approach: 236500 ms
Ratio: Vector Space Model approach is in overall 195.03 times faster than Linear Search approach.


As we can see, vector space model approach is much faster (195 times) than linear search approach. 
This is because:
1. Vector space model approach is based on matrix operations.
2. Linear search approach is based on string operations.